# Ising Belief Propagation

In [1]:
using LaTeXStrings
using Plots

INFO: Recompiling stale cache file /Network/Servers/mac25.thp.uni-koeln.de/Volumes/RAID/skleinbo/.julia/lib/v0.6/LaTeXStrings.ji for module LaTeXStrings.
INFO: Recompiling stale cache file /Network/Servers/mac25.thp.uni-koeln.de/Volumes/RAID/skleinbo/.julia/lib/v0.6/Plots.ji for module Plots.


In [2]:
gr()

Plots.GRBackend()

## Define methods

In [3]:
"""
Magnetization of a homogeneous Ising chain
with coupling `J` and external field `h`
at temperature β
"""
m_Chain(β,J,h) = begin 
    s = sinh(β*h)
    c = cosh(β*h)
    e = exp(-4β*J)
    (s + s*c/sqrt(s^2+e))/(c + sqrt(s^2+e))
end

m_Chain

In [4]:
"""
Returns the coupling matrix for a homogeneous 1d Ising chain
of length `n` of unit coupling strength
"""
function makeJring(n)
    Jring = diagm(ones(n-1),1) # 1s on the first off-diagonal
    Jring[1,n] = 1  # PBC
    return Jring = (Jring+Jring'); # symmetrize
end

makeJring

In [5]:
"""
Construct coupling matrix of unit strength
for a 2d square lattice with 
open boundary conditions
of size `nxn`
"""
function makeJsq(n)
    N = n^2
    Jsq = zeros(N,N);
    for k in 1:N
        if k+1<=N && k%n>0      
            Jsq[k,k+1] = 1.
        end
        if k+n<=N
            Jsq[k,k+n] = 1.
        end
    end
    Jsq = Jsq+Jsq';
end

makeJsq

In [6]:
"""
Function to perform the belief propagation.

Ends when either `MaxIter` is reached or until convergence with error `err`.

Arguments: 
`H`: Initial message state; get's mutated  
`β`: Inverse temperature  
`J`: Coupling matrix  
`h`: field vector 
"""
function BP!(H,β,J,h;err=1e-8,MaxIter=1000)
    iter = 0
    converged = false
    N = size(J,1)

    while iter<MaxIter && !converged  

        diff = 0.
        for j in 1:N
            # Sum over incoming messages
            for i in 1:N

                sum = 0.
                for k in 1:N
                    if j==k
                        continue
                    end
                    sum += H[k,i]
                end

                if i==j
                    continue
                end
                new_hij = h[j]/N + 1/β * atanh( tanh(β*J[i,j])*tanh(β*sum))
                diff = max(diff, abs(H[i,j]-new_hij))
                H[i,j] = new_hij
            end
        end

        converged = diff <= err
        iter +=1
    end
    
    if !converged 
        println("no convergence after $MaxIter iterations!")
    end
    return sum(H,1)[1,:]
end

BP!

In [7]:
"""
Run the algorithm on a ring for a range of temperatures and
field strength `h`.

Initializes the messages itself.

Returns the magnetization over temperature. 
Magnetization is taken in the middle of the ring, but for PBC this should be inconsequential.
"""
function getMagRing(n,h,βs;kw...)
    hh = fill(h,n)
    M = Float64[]

    J = makeJring(n)
    
    H = zeros(n,n)
    H[1,2] = 1.
    H[n,1] = 1.

    return map(βs) do x
        tanh(x*(BP!(copy(H),x,J,hh,kw...)[div(n,2)]))
    end
    
end

getMagRing

In [8]:
"""
Run the algorithm on a square lattice for a range of temperatures
field strength `h`.

Initializes the messages to one, except the self-messages which are
set to zero.

Return the magnetization tanh(βH_i) as measured in the center of the lattice. 
"""
function getMagSquare(n,h,βs;kw...)
    N = n^2
    hh = fill(h,N)
    J = makeJsq(n)

    H = ones(N,N) - eye(Float64,N)
    
    return begin
        map(βs) do β
            tanh(β*(BP!(copy(H),β,J,hh;kw...)[div(N,2)]))
        end
    end
end

getMagSquare

## Data analysis

__Generate data__

In [24]:
βs = linspace(0.35,0.45,25) # temperature range
n = 10 # linear system size
hh = [0.0,] # external field strengths

## M has as columns the magnetization at a given field strength as a function of temperature
## for BP on a ring replace `getMagSquare` with `getMagRing`
M = reduce(hcat,map(h->getMagSquare(n,h,βs,MaxIter=4000), hh));

no convergence after 4000 iterations!


__Critical temperature__: between temps where magnetization is practically zero and not
    

In [22]:
βc = βs[findfirst(x->x>1e-4,M)]/2 + βs[findlast(x->x<1e-4,M)]/2
1/βc

2.6815642458100557

__Visualize__

In [26]:
plot(βs,M,marker=(:auto,3),lab=["h=$h" for h in hh], lw=0, leg=:topleft)
vline!([βc], linestyle=:dash, lab=L"$ \beta_c $", lab=L"\beta_c")
xlabel!(L"\beta")
ylabel!("m")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.36 
 
 
 0.38 
 
 
 0.40 
 
 
 0.42 
 
 
 0.44 
 
 
 0.00 
 
 
 0.25 
 
 
 0.50 
 
 
 
 
 
 m 
 
<polyline clip-path="url(#clip02)" style="stroke:#009af9; stroke-width:0; stroke-opacity:1; fill:none" points="
 55.0141,348.669 76.7419,348.669 98.4698,348.669 120.198,348.669 141.925,348.669 163.653,348.669 185.381,345.004 207.109,278.431 228.837,247.942 250.565,223.915 
 272.292,203.223 294.02,184.699 315.748,167.76 337.476,152.072 359.204,137.42 380.932,123.656 402.659,110.674 424.387,98.3921 446.115,86.745 467.843,75.6798 
 489.571,65.1517 511.298,55.1224 533.026,45.5582 554.754,36.4294 576.482,27.7093 
 "/>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 h=0.0